On va commencer par installer un serveur mongodb

In [1]:
!apt install -y gnupg curl
!curl -fsSL https://pgp.mongodb.com/server-7.0.asc | sudo gpg -o /usr/share/keyrings/mongodb-server-7.0.gpg --dearmor
!echo "deb [ arch=amd64,arm64 signed-by=/usr/share/keyrings/mongodb-server-7.0.gpg ] https://repo.mongodb.org/apt/ubuntu jammy/mongodb-org/7.0 multiverse" | sudo tee /etc/apt/sources.list.d/mongodb-org-7.0.list
!sudo apt update
!sudo apt install -y mongodb-org

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
curl is already the newest version (7.81.0-1ubuntu1.21).
gnupg is already the newest version (2.2.27-3ubuntu2.4).
gnupg set to manually installed.
0 upgraded, 0 newly installed, 0 to remove and 38 not upgraded.
deb [ arch=amd64,arm64 signed-by=/usr/share/keyrings/mongodb-server-7.0.gpg ] https://repo.mongodb.org/apt/ubuntu jammy/mongodb-org/7.0 multiverse
Hit:1 https://cli.github.com/packages stable InRelease
Hit:2 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:3 https://repo.mongodb.org/apt/ubuntu jammy/mongodb-org/7.0 InRelease [3,005 B]
Get:4 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,632 B]
Get:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Hit:6 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Get:7 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Get:8 http://archive.ubuntu.com/ubuntu jammy-backports InRele

On lance le serveur

In [2]:
!mkdir -p /data/db
!mongod --fork --logpath /tmp/mongod.log --dbpath /data/db

about to fork child process, waiting until server is ready for connections.
forked process: 1304
child process started successfully, parent exiting


Installation de pymongo

In [3]:
%pip install pymongo

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 24.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 331.1/331.1 kB 26.8 MB/s eta 0:00:00


Et on fait un petit test

In [4]:
from pymongo import MongoClient

# Connect to the MongoDB server (default port is 27017)
client = MongoClient('mongodb://localhost:27017/')

# Create or connect to a database
db = client['mydatabase']

# Create or connect to a collection (similar to a table in relational databases)
mycollection = db['mycollection']

# Insert a document into the collection
my_document = { "name": "Alice", "age": 30 }
inserted_doc = mycollection.insert_one(my_document)
print(f"Inserted document ID: {inserted_doc.inserted_id}")

# Query the collection
found_document = mycollection.find_one({ "name": "Alice" })
print(f"Found document: {found_document}")

# You can insert multiple documents as well
my_documents = [
    { "name": "Bob", "age": 25 },
    { "name": "Charlie", "age": 35 }
]
inserted_docs = mycollection.insert_many(my_documents)
print(f"Inserted multiple document IDs: {inserted_docs.inserted_ids}")

# Find all documents in the collection
all_documents = mycollection.find()
print("All documents in the collection:")
for doc in all_documents:
    print(doc)

# Close the connection
client.close()

Inserted document ID: 68e75e38eef716162daa8fd1
Found document: {'_id': ObjectId('68e75e38eef716162daa8fd1'), 'name': 'Alice', 'age': 30}
Inserted multiple document IDs: [ObjectId('68e75e38eef716162daa8fd2'), ObjectId('68e75e38eef716162daa8fd3')]
All documents in the collection:
{'_id': ObjectId('68e75e38eef716162daa8fd1'), 'name': 'Alice', 'age': 30}
{'_id': ObjectId('68e75e38eef716162daa8fd2'), 'name': 'Bob', 'age': 25}
{'_id': ObjectId('68e75e38eef716162daa8fd3'), 'name': 'Charlie', 'age': 35}


Vérification que le serveur tourne toujours

In [5]:
!ps aux | grep mongod

root        1304  1.1  0.9 543860 121216 ?       Sl   07:02   0:00 mongod --fork --logpath /tmp/mongod.log --dbpath /data/db
root        1532  0.0  0.0   7376  3328 ?        S    07:03   0:00 /bin/bash -c ps aux | grep mongod
root        1534  0.0  0.0   6484  2304 ?        S    07:03   0:00 grep mongod


Maintenant on monte son Google Drive. Il ne faut pas oublier de créer un dossier nommé `m1_csmi_sgdb` à la racine du Drive. Il faut aussi accepter l'accès au Drive (les accès par défaut suffisent).

In [32]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


On crée un fichier `veterinaire.db` (attention, s'il existe, il est écrasé) et on se connecte à cette base de données vide.

In [33]:
import sqlite3
import pandas as pd
import os

new_db_path = '/content/drive/MyDrive/m1_csmi_sgdb/veterinaire.db'
# on commence par supprimer le fichier pour un démarrage propre
if os.path.exists(new_db_path):
    os.remove(new_db_path)
    print(f"Existing database file '{new_db_path}' removed.")

connect = sqlite3.connect(new_db_path)
print("Database created and Successfully Connected to SQLite")

Existing database file '/content/drive/MyDrive/m1_csmi_sgdb/veterinaire.db' removed.
Database created and Successfully Connected to SQLite


Petit test de manipulations SQL.

In [28]:
cursor = connect.cursor()

# Create the 'animal' table
create_table_sql = """
CREATE TABLE animal (
    id INTEGER PRIMARY KEY,
    nom TEXT NOT NULL,
    espece TEXT NOT NULL,
    age INTEGER
);
"""
cursor.execute(create_table_sql)
print("Table 'animal' created successfully.")

# Insert data into the 'animal' table
insert_data_sql = """
INSERT INTO animal (nom, espece, age)
VALUES ('Rex', 'Chien', 5);
"""
cursor.execute(insert_data_sql)

insert_data_sql = """
INSERT INTO animal (nom, espece, age)
VALUES ('Miaou', 'Chat', 3);
"""
cursor.execute(insert_data_sql)

insert_data_sql = """
INSERT INTO animal (nom, espece, age)
VALUES ('Panpan', 'Lapin', 2);
"""
cursor.execute(insert_data_sql)
print("Data inserted successfully into 'animal' table.")
connect.commit()

Table 'animal' created successfully.
Data inserted successfully into 'animal' table.


In [29]:
#display animal table
df = pd.read_sql_query("SELECT * FROM animal", connect)
df

id     nom espece  age
0   1     Rex  Chien    5
1   2   Miaou   Chat    3
2   3  Panpan  Lapin    2

In [31]:
#close the connection
connect.close()